**Retrieval-Augmented Generation (RAG)** is a method that integrates information retrieval to give generative language models additional information. 

**A typical RAG pipeline comprises of 2 main components:**

1. a **Retriever Module** that first selects relevant documents or pieces of information from a large corpus based on the input query,
2. an **Answer Generation Module** that produces more accurate and contextually relevant responses.

#### Steps to implement a RAG pipeline (Part 1/2):
1. Indexing Documents

2. Creating Embeddings

3. Create a vector store and store embeddings

In [4]:
pip install langchain langchain-community langchain-core langchain-openai langchain-text-splitters openai bs4 chromadb python-dotenv colorama tqdm tiktoken httplib2


Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 96 kB 4.9 MB/s eta 0:00:01
  Using cached pyparsing-3.1.2-py3-none-any.whl (103 kB)
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [5]:

from dotenv import load_dotenv
from colorama import Fore
import warnings
warnings.filterwarnings("ignore")

load_dotenv()

False

1. Load and split documents

Paul Graham is known for his influential essays on startups, technology, programming, and life in general. He is a co-founder of Y Combinator, a prominent startup accelerator, and has written numerous essays that have inspired many entrepreneurs and technologists. 

In [53]:
from langchain_community.document_loaders import WebBaseLoader
from langchain.text_splitter import CharacterTextSplitter 

url = 'https://www.paulgraham.com/articles.html'
def load_documents():
    """Load a file from path, split it into chunks, embed each chunk and load it into the vector store."""
    loader = WebBaseLoader("https://www.paulgraham.com/persistence.html")
    raw_text = loader.load()
    splitter = CharacterTextSplitter(chunk_size=100, chunk_overlap=0)
    return splitter.split_documents(raw_text)

documents = load_documents()
print(f"Loaded {len(documents)} documents")

Created a chunk of size 11382, which is longer than the specified 100


Loaded 2 documents


2. Create vector store and store embeddings

In [54]:
from langchain_community.embeddings import OpenAIEmbeddings
from langchain_community.vectorstores import Chroma
from openai import OpenAI
from dotenv import load_dotenv
import os

load_dotenv()

client = OpenAI(api_key=os.getenv("OPENAI_API_KEY"))

def get_embedding(text_to_embed):
    response = client.embeddings.create(
        model= "text-embedding-ada-002",
        input=[text_to_embed]
    )
    print(response.data[0].embedding)

def load_embeddings(user_query, documents):
    """Create a vector store from a set of documents."""
    embeddings = OpenAIEmbeddings()
    db = Chroma.from_documents(documents, embeddings)
    get_embedding(user_query)
    _ = [get_embedding(doc.page_content) for doc in documents]
    return db.as_retriever()

retriever = load_embeddings("I have an error code E2", documents)

[-0.015627305954694748, -0.0038546891883015633, -0.015446563251316547, -0.024010995402932167, -0.028390534222126007, 0.014181363396346569, -0.023232409730553627, -0.010239779017865658, -0.003701752983033657, -0.00817513931542635, 0.007980492897331715, 0.0031612622551620007, 0.0014546324964612722, -0.005293680354952812, -0.0187972579151392, 0.00027133154799230397, 0.006451129913330078, 0.01373645756393671, 0.012652000412344933, -0.005749013740569353, -0.004056286998093128, 0.0016136515187099576, -0.013812926597893238, -0.006944697350263596, 0.006013176403939724, -0.014487235806882381, 0.003216875484213233, -0.017420832067728043, -0.016405891627073288, -0.014807011932134628, 0.012777130119502544, -0.026916783303022385, -0.022968247532844543, -0.043656352907419205, -0.028181985020637512, -0.004876581486314535, -0.019979039207100868, 0.001525886938907206, 0.022008920088410378, -0.01136594545096159, 0.04852250963449478, 0.013131664134562016, -0.0107681043446064, -0.010705539025366306, -0.02

#### Steps to implement a RAG pipeline (Part 2/2):
1. Define a prompt
2. Create and run the retrieval chain


In [55]:
from langchain_openai import ChatOpenAI
from langchain.prompts.chat import (
    HumanMessagePromptTemplate,
    SystemMessagePromptTemplate,
)
from langchain.prompts import ChatPromptTemplate, PromptTemplate

template: str = """/
    Paul Graham is known for his influential essays on startups, technology, programming, 
    and life in general. He is a co-founder of Y Combinator, a prominent startup accelerator, 
    and has written numerous essays that have inspired many entrepreneurs and technologists.
    You assist users with general inquiries and {question} based on {context} /
    """
system_message_prompt = SystemMessagePromptTemplate.from_template(template)
human_message_prompt = HumanMessagePromptTemplate.from_template(
    input_variables=["question", "context"],
    template="{question}",
)
chat_prompt_template = ChatPromptTemplate.from_messages(
    [system_message_prompt, human_message_prompt]
)

model = ChatOpenAI()

2. Create and run the chain

In [57]:
from langchain.schema import StrOutputParser
from langchain.schema.runnable import RunnablePassthrough

def generate_response(query):
    """Generate a response using the retriever and the query."""
    # Create a prompt template using a template from the config module and input variables
    # representing the context and question.
    # create the prompt
    chain = (
        {"question": RunnablePassthrough(), "context": retriever} 
        | chat_prompt_template
        | model 
        | StrOutputParser()
    )
    return chain.invoke(query)


#### Chunking Strategies :
1. Simplest chunking method with **CharacterTextSplitter**
2. Text division without word bounderies with **RecursiveCharacterTextSplitter**
3. Smart Text Division with **Semantic Splitting**

<span style="color:#8e44ad">Try it Out!</span>

In [58]:

response = generate_response("What is the best way to learn programming?")
print(f"{Fore.GREEN}{response}{Fore.RESET}")

The best way to learn programming is to adopt a persistent and determined mindset, as outlined in Paul Graham's essay "The Right Kind of Stubborn." Here are some key points from the essay that can guide you in learning programming effectively:

1. **Persistence over Obstinance**: Successful people tend to be persistent, not obstinate. Persistence involves listening, learning, and adapting, while obstinance is a blind resistance to change. When learning programming, be open to new ideas, feedback, and different approaches.

2. **Energy and Imagination**: To excel in programming, you need both energy and imagination. Energy will drive you to keep trying and learning, while imagination will help you come up with creative solutions to problems.

3. **Resilience and Good Judgement**: Resilience is essential in programming, as setbacks are common. Good judgement will help you make informed decisions and focus on what's most important in your learning journey.

4. **Focus on a Goal**: Have a 

In [35]:
pip install httplib2

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [74]:
import httplib2
from bs4 import BeautifulSoup, SoupStrainer

http = httplib2.Http()

def get_links(url):
    status, response = http.request(url)
    links = []
    for link in BeautifulSoup(response, parse_only=SoupStrainer('a')):
        if link.has_attr('href'):
            links.append(f"https://www.paulgraham.com/{link.attrs['href']}")
    return links

1. CharacterTextSplitter

In [87]:

links = get_links(url)
print(links)
loader = WebBaseLoader(links)



['https://www.paulgraham.com/index.html', 'https://www.paulgraham.com/wisdom.html', 'https://www.paulgraham.com/kids.html', 'https://www.paulgraham.com/selfindulgence.html', 'https://www.paulgraham.com/persistence.html', 'https://www.paulgraham.com/reddits.html', 'https://www.paulgraham.com/google.html', 'https://www.paulgraham.com/best.html', 'https://www.paulgraham.com/superlinear.html', 'https://www.paulgraham.com/greatwork.html', 'https://www.paulgraham.com/getideas.html', 'https://www.paulgraham.com/read.html', 'https://www.paulgraham.com/want.html', 'https://www.paulgraham.com/alien.html', 'https://www.paulgraham.com/users.html', 'https://www.paulgraham.com/heresy.html', 'https://www.paulgraham.com/words.html', 'https://www.paulgraham.com/goodtaste.html', 'https://www.paulgraham.com/smart.html', 'https://www.paulgraham.com/weird.html', 'https://www.paulgraham.com/hwh.html', 'https://www.paulgraham.com/own.html', 'https://www.paulgraham.com/fn.html', 'https://www.paulgraham.com/ne

In [94]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

raw_text = loader.load()
splitter = RecursiveCharacterTextSplitter(chunk_size=300, chunk_overlap=0, separators=["\n\n"])
documents = splitter.split_documents(raw_text)
print(f"Loaded {len(documents)} documents")
print("--------------")
_ = [print(f"Document {index} \n ------- {doc.page_content}") for index, doc in enumerate(documents)]

embeddings = OpenAIEmbeddings()
db = Chroma.from_documents(documents, embeddings)
retriever = db.as_retriever()


Loaded 825 documents
--------------
Document 0 
 ------- 
 Paul Graham



New:

The Right Kind of Stubborn |
Google |
Superlinear





Want to start a startup? Get funded by Y Combinator.









© mmxxiv pg
Document 1 
 ------- 
 Is It Worth Being Wise?
Document 2 
 ------- 
 

February 2007A few days ago I finally figured out something I've wondered about
for 25 years: the relationship between wisdom and intelligence.
Anyone can see they're not the same by the number of people who are
smart, but not very wise.  And yet intelligence and wisdom do seem
related.  How?What is wisdom?  I'd say it's knowing what to do in a lot of
situations.  I'm not trying to make a deep point here about the
true nature of wisdom, just to figure out how we use the word.  A
wise person is someone who usually knows the right thing to do.And yet isn't being smart also knowing what to do in certain
situations?  For example, knowing what to do when the teacher tells
your elementary school class to add all the

In [95]:

def generate_response(query):
    """Generate a response using the retriever and the query."""
    # Create a prompt template using a template from the config module and input variables
    # representing the context and question.
    # create the prompt
    chain = (
        {"context": retriever, "question": RunnablePassthrough()} 
        | chat_prompt_template 
        | model 
        | StrOutputParser()
    )
    return chain.invoke(query)

<span style="color:#8e44ad">Try it Out!</span>

In [96]:
response = generate_response("How do I learn programming?")
print(f"{Fore.GREEN}{response}{Fore.RESET}")

Learning programming involves a combination of practice, problem-solving, and continuous learning. Here are some steps to help you get started with learning programming:

1. **Choose a Programming Language**: Start by selecting a programming language to learn. Popular languages for beginners include Python, JavaScript, and Java. Each language has its own strengths and use cases, so choose one that aligns with your interests and goals.

2. **Online Resources and Courses**: Utilize online resources like freeCodeCamp, Codecademy, Coursera, edX, and YouTube tutorials to learn the basics of programming. These platforms offer structured courses and tutorials for beginners.

3. **Practice Coding**: The best way to learn programming is by practicing writing code regularly. Start with small projects and gradually work your way up to more complex programs. Practice is key to improving your coding skills.

4. **Work on Projects**: Create your own projects to apply what you've learned. Building pr

2. RecursiveCharacterTextSplitter

In [101]:
splitter = RecursiveCharacterTextSplitter(chunk_size=300, chunk_overlap=0, separators=["\n\n"])
documents = splitter.split_documents(raw_text)
print(f"Loaded {len(documents)} documents")
print("--------------")
_ = [print(f"Document {index} \n ------- \n {doc.page_content}") for index, doc in enumerate(documents)]

embeddings = OpenAIEmbeddings()
db = Chroma.from_documents(documents, embeddings)
retriever = db.as_retriever()


Loaded 825 documents
--------------
Document 0 
 ------- 
 Paul Graham



New:

The Right Kind of Stubborn |
Google |
Superlinear





Want to start a startup? Get funded by Y Combinator.









© mmxxiv pg
Document 1 
 ------- 
 Is It Worth Being Wise?
Document 2 
 ------- 
 

February 2007A few days ago I finally figured out something I've wondered about
for 25 years: the relationship between wisdom and intelligence.
Anyone can see they're not the same by the number of people who are
smart, but not very wise.  And yet intelligence and wisdom do seem
related.  How?What is wisdom?  I'd say it's knowing what to do in a lot of
situations.  I'm not trying to make a deep point here about the
true nature of wisdom, just to figure out how we use the word.  A
wise person is someone who usually knows the right thing to do.And yet isn't being smart also knowing what to do in certain
situations?  For example, knowing what to do when the teacher tells
your elementary school class to add all the

<span style="color:#8e44ad">Try it Out!</span>

In [100]:
response = generate_response("How do I learn programming?")
print(f"{Fore.GREEN}{response}{Fore.RESET}")

Learning programming can be a rewarding and valuable skill. Here are some tips on how to learn programming effectively:

1. **Start with the Basics**: Begin by learning the fundamental concepts of programming, such as variables, data types, loops, functions, and conditional statements. Understanding these basics will provide a strong foundation for more advanced topics.

2. **Choose a Programming Language**: Select a programming language to start learning. Some popular languages for beginners include Python, Java, JavaScript, and C++. Each language has its own strengths and use cases, so choose one that aligns with your goals.

3. **Online Courses and Tutorials**: There are numerous online platforms like Codecademy, Coursera, edX, and Khan Academy that offer courses for beginners to learn programming. These courses provide structured learning paths and interactive exercises to help you grasp programming concepts.

4. **Practice, Practice, Practice**: Programming is a skill that require

2. Semantic Splitting

In [103]:
pip install --quiet langchain_experimental langchain_openai

3988.86s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [112]:
from langchain_experimental.text_splitter import SemanticChunker

splitter = SemanticChunker( OpenAIEmbeddings(), breakpoint_threshold_type="percentile")
documents = splitter.split_documents(raw_text)
print(f"Loaded {len(documents)} documents")
print("--------------")
_ = [print(f"Document {index} \n -------- \n {doc.page_content}") for index, doc in enumerate(documents)]
print(documents)
db = Chroma.from_documents(documents, OpenAIEmbeddings())
retriever = db.as_retriever()


KeyboardInterrupt: 

<span style="color:#8e44ad">Try it Out!</span>

In [110]:
response = generate_response("How do I learn programming?")
print(f"{Fore.GREEN}{response}{Fore.RESET}")

Learning programming can be a rewarding and fulfilling experience. Here are some tips based on Paul Graham's essay "Let the Other 95% of Great Programmers In":

1. **Start with a simple language**: Begin with a language that is easy to learn and understand, such as Python. It has a clean syntax and is widely used for various applications.

2. **Write lots of code**: The best way to learn programming is by writing code. Start with small projects and gradually increase the complexity as you gain more experience.

3. **Read code written by others**: Studying code written by experienced programmers can help you learn new techniques and best practices. Open-source projects on platforms like GitHub are a great resource for this.

4. **Work on real projects**: Apply your programming skills to real-world projects, whether personal or for a job. This hands-on experience will help you improve your problem-solving abilities.

5. **Seek feedback**: Don't be afraid to show your code to others and a

**Documentation**: [How to split text based on semantic similarity](https://python.langchain.com/v0.2/docs/how_to/semantic-chunker/) 